<h1><center>Laboratorio 6: Optimización de modelos 🧪</center></h1>

<center><strong>MDS7202: Laboratorio de Programación Científica para Ciencia de Datos - Primavera 2025</strong></center>

### Cuerpo Docente:

- Profesores: Diego Cortez, Gabriel Iturra
- Auxiliares: Melanie Peña, Valentina Rojas
- Ayudantes: Nicolás Cabello, Cristopher Urbina

### Equipo: SUPER IMPORTANTE - notebooks sin nombre no serán revisados

- Nombre de alumno 1: Diego Acuña
- Nombre de alumno 2: Tomás Ramírez


Reglas:

- **Grupos de 2 personas**
- Fecha de entrega: Entregas Martes a las 23:59.
- Instrucciones del lab el viernes a las 16:15 en formato online. Asistencia no es obligatoria, pero se recomienda **fuertemente** asistir.
- <u>Prohibidas las copias</u>. Cualquier intento de copia será debidamente penalizado con el reglamento de la escuela.
- Tienen que subir el laboratorio a u-cursos y a su repositorio de github. Labs que no estén en u-cursos no serán revisados. Recuerden que el repositorio también tiene nota.
- Cualquier duda fuera del horario de clases al foro. Mensajes al equipo docente serán respondidos por este medio.
- Pueden usar cualquier material del curso que estimen conveniente.

### **Link de repositorio de GitHub:** [Insertar Repositorio](https://github.com/Diego-Acuna/mds-laboratorios.git)

### Temas a tratar

- Predicción de demanda usando `xgboost`
- Búsqueda del modelo óptimo de clasificación usando `optuna`
- Uso de pipelines.


### Reglas:

- **Grupos de 2 personas**
- Fecha de entrega: 6 días de plazo con descuento de 1 punto por día. Entregas Martes a las 23:59.
- Instrucciones del lab el viernes a las 16:15 en formato online. Asistencia no es obligatoria, pero se recomienda fuertemente asistir.
- <u>Prohibidas las copias</u>. Cualquier intento de copia será debidamente penalizado con el reglamento de la escuela.
- Tienen que subir el laboratorio a u-cursos y a su repositorio de github. Labs que no estén en u-cursos no serán revisados. Recuerden que el repositorio también tiene nota.
- Cualquier duda fuera del horario de clases al foro. Mensajes al equipo docente serán respondidos por este medio.
- Pueden usar cualquier material del curso que estimen conveniente.

El laboratorio deberá ser desarrollado sin el uso indiscriminado de iteradores nativos de python (aka "for", "while"). La idea es que aprendan a exprimir al máximo las funciones optimizadas que nos entrega `pandas`, las cuales vale mencionar, son bastante más eficientes que los iteradores nativos sobre DataFrames.

# Importamos librerias útiles

In [52]:
!pip install -qq xgboost optuna

In [53]:
!pip install xgboost==2.0.3

# El emprendimiento de Fiu

Tras liderar de manera exitosa la implementación de un proyecto de ciencia de datos para caracterizar los datos generados en Santiago 2023, el misterioso corpóreo **Fiu** se anima y decide levantar su propio negocio de consultoría en machine learning. Tras varias e intensas negociaciones, Fiu logra encontrar su *primera chamba*: predecir la demanda (cantidad de venta) de una famosa productora de bebidas de calibre mundial. Al ver el gran potencial y talento que usted ha demostrado en el campo de la ciencia de datos, Fiu lo contrata como data scientist para que forme parte de su nuevo emprendimiento.

Para este laboratorio deben trabajar con los datos `sales.csv` subidos a u-cursos, el cual contiene una muestra de ventas de la empresa para diferentes productos en un determinado tiempo.

Para comenzar, cargue el dataset señalado y visualice a través de un `.head` los atributos que posee el dataset.

<i><p align="center">Fiu siendo felicitado por su excelente desempeño en el proyecto de caracterización de datos</p></i>
<p align="center">
  <img src="https://media-front.elmostrador.cl/2023/09/A_UNO_1506411_2440e.jpg">
</p>

In [54]:
import pandas as pd
import numpy as np
from datetime import datetime

df = pd.read_csv('./sales.csv')

df.head()

id      date    city       lat      long     pop    shop        brand  \
0   0  31/01/12  Athens  37.97945  23.71622  672130  shop_1  kinder-cola   
1   1  31/01/12  Athens  37.97945  23.71622  672130  shop_1  kinder-cola   
2   2  31/01/12  Athens  37.97945  23.71622  672130  shop_1  kinder-cola   
3   3  31/01/12  Athens  37.97945  23.71622  672130  shop_1   adult-cola   
4   4  31/01/12  Athens  37.97945  23.71622  672130  shop_1   adult-cola   

  container capacity  price  quantity  
0     glass    500ml   0.96     13280  
1   plastic    1.5lt   2.86      6727  
2       can    330ml   0.87      9848  
3     glass    500ml   1.00     20050  
4       can    330ml   0.39     25696

## 1 Generando un Baseline (5 puntos)

<p align="center">
  <img src="https://media.tenor.com/O-lan6TkadUAAAAC/what-i-wnna-do-after-a-baseline.gif">
</p>

Antes de entrenar un algoritmo, usted recuerda los apuntes de su magíster en ciencia de datos y recuerda que debe seguir una serie de *buenas prácticas* para entrenar correcta y debidamente su modelo. Después de un par de vueltas, llega a las siguientes tareas:

1. Separe los datos en conjuntos de train (70%), validation (20%) y test (10%). Fije una semilla para controlar la aleatoriedad. [0.5 puntos]
2. Implemente un `FunctionTransformer` para extraer el día, mes y año de la variable `date`. Guarde estas variables en el formato categorical de pandas. [1 punto]
3. Implemente un `ColumnTransformer` para procesar de manera adecuada los datos numéricos y categóricos. Use `OneHotEncoder` para las variables categóricas. `Nota:` Utilice el método `.set_output(transform='pandas')` para obtener un DataFrame como salida del `ColumnTransformer` [1 punto]
4. Guarde los pasos anteriores en un `Pipeline`, dejando como último paso el regresor `DummyRegressor` para generar predicciones en base a promedios. [0.5 punto]
5. Entrene el pipeline anterior y reporte la métrica `mean_absolute_error` sobre los datos de validación. ¿Cómo se interpreta esta métrica para el contexto del negocio? [0.5 puntos]
6. Finalmente, vuelva a entrenar el `Pipeline` pero esta vez usando `XGBRegressor` como modelo **utilizando los parámetros por default**. ¿Cómo cambia el MAE al implementar este algoritmo? ¿Es mejor o peor que el `DummyRegressor`? [1 punto]
7. Guarde ambos modelos en un archivo .pkl (uno cada uno) [0.5 puntos]

In [55]:
# Código entregado
from sklearn import set_config
set_config(transform_output="pandas")

# Importamos librerías necesarias
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import FunctionTransformer
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.dummy import DummyRegressor
from sklearn.metrics import mean_absolute_error
from xgboost import XGBRegressor
import joblib

# ================== Pregunta 1 ==================

# Definimos X e y
target = "quantity"
X = df.drop(columns=[target, "id"])  # quitamos 'id' por ser un identificador
y = df[target]

# Definimos una semilla para la reproducibilidad
SEED = 42

# Separamos primero el test (10%)
X_trainval, X_test, y_trainval, y_test = train_test_split(
    X, y, test_size=0.10, random_state=SEED
)

# A continuación separamos el conjunto de entrenamiento y el de validación
val_size = 0.2/0.9
X_train, X_val, y_train, y_val = train_test_split(
    X_trainval, y_trainval, test_size=val_size, random_state=SEED
)

# ================== Pregunta 2 ==================

# Definimos una función que toma un DataFrame con columna "date", agreega day/month/year y elimina "date"
def add_date_parts(X_df: pd.DataFrame) -> pd.DataFrame:
    X_df = X_df.copy()
    
    # Hacemos un parseo para obtener las fechas en formato DD/MM/YY
    d = pd.to_datetime(X_df["date"], format='%d/%m/%y', dayfirst=True, errors="coerce")
    
    # Extraemos partes y las guardamos como categóricas de pandas
    X_df["day"] = pd.Categorical(d.dt.day)
    X_df["month"] = pd.Categorical(d.dt.month)
    X_df["year"] = pd.Categorical(d.dt.year)
    
    # Eliminamos la columna original
    X_df = X_df.drop(columns=["date"])
    return X_df

# Lo envolvemos en un FunctionTransformer para integrarlo al Pipeline luego
date_ft = FunctionTransformer(add_date_parts)

# ================= Pregunta 3 ==================

# Definimos las columnas categóricas y numéricas
numeric_cols = ["lat", "long", "pop", "price"]
categorical_cols = ["city", "shop", "brand", "container", "capacity", "day", "month", "year"]

# Definimos el ColumnTransformer
preprocess = ColumnTransformer(
    transformers=[
        ("num", StandardScaler(), numeric_cols),  # Aplicamos StandardScaler a las columnas numéricas
        ("cat", OneHotEncoder(handle_unknown="ignore", sparse_output=False), categorical_cols)  # Aplicamos OneHotEncoder a las categóricas
    ],
    remainder="drop"
)

# ================ Pregunta 4 ==================

# Definimos el Pipeline completo
pipeline_dummy = Pipeline(steps=[
    ("date_ft", date_ft),          
    ("preprocess", preprocess),      
    ("model", DummyRegressor(strategy="mean"))
])

# =============== Pregunta 5 ==================

# Entrenamos el modelo con el DummyRegressor
pipeline_dummy.fit(X_train, y_train)

# Hacemos predicciones en el conjunto de validación
y_val_pred_dummy = pipeline_dummy.predict(X_val)

# Evaluamos el MAE
mae_dummy = mean_absolute_error(y_val, y_val_pred_dummy)

# Mostramos el MAE en pantalla
print(f"MAE validación (DummyRegressor): {mae_dummy:.3f}")

# =============== Pregunta 6 ==================

# Definimos el Pipeline con XGBRegressor utilizando los parámetros por default
pipeline_xgb = Pipeline(steps=[
    ("date_ft", date_ft),          
    ("preprocess", preprocess),      
    ("model", XGBRegressor(random_state=SEED))
])

# Entrenamos el modelo con XGBRegressor
pipeline_xgb.fit(X_train, y_train)

# Hacemos predicciones en el conjunto de validación
y_val_pred_xgb = pipeline_xgb.predict(X_val)

# Evaluamos el MAE
mae_xgb = mean_absolute_error(y_val, y_val_pred_xgb)

# Mostramos el MAE en pantalla
print(f"MAE validación (XGBRegressor default): {mae_xgb:.3f}")

# =============== Pregunta 7 ==================

# Guardamos los archivos en un .pkl
joblib.dump(pipeline_dummy, 'pipeline_dummy.pkl')
joblib.dump(pipeline_xgb, 'pipeline_xgb.pkl')

MAE validación (DummyRegressor): 13543.961
MAE validación (XGBRegressor default): 2402.355


['pipeline_xgb.pkl']

**Respuestas:**

**Pregunta 5:** Esta métrica mide el promedio del error absoluto entre lo predicho y lo real, en las mismas unidadese que la variable objetivo (quantity). Por ejemplo, en el caso del DummyRegressor, como la MAE=$13543$, esto significa que en promedio el modelo se está equivocando en $13543$ unidades por registro. Es relevante mencionar que no importa si se sobre o sub-predice, pues solo se mide la magnitud del error.

**Pregunta 6:** El MAE disminuye considerablemente con el XGBRegressor, lo cual significa que este modelo es mejor que el DummyRegressor. Esto es evidente pues el DummyRegressor se basa en aleatoriedad, mientras que el XGBRegressor busca establecer relaciones entre las features y la variable objetivo.

## 2. Forzando relaciones entre parámetros con XGBoost (10 puntos)

<p align="center">
  <img src="https://64.media.tumblr.com/14cc45f9610a6ee341a45fd0d68f4dde/20d11b36022bca7b-bf/s640x960/67ab1db12ff73a530f649ac455c000945d99c0d6.gif">
</p>

Un colega aficionado a la economía le *sopla* que la demanda guarda una relación inversa con el precio del producto. Motivado para impresionar al querido corpóreo, se propone hacer uso de esta información para mejorar su modelo realizando las siguientes tareas:

1. Vuelva a entrenar el `Pipeline` con `XGBRegressor`, pero esta vez forzando una relación monótona negativa entre el precio y la cantidad. Para aplicar esta restricción apóyese en la siguiente <a href = https://xgboost.readthedocs.io/en/stable/tutorials/monotonic.html>documentación</a>. [6 puntos]

>Hint 1: Para implementar el constraint se le sugiere hacerlo especificando el nombre de la variable. De ser así, probablemente le sea útil **mantener el formato de pandas** antes del step de entrenamiento.

>Hint 2: Puede obtener el nombre de las columnas en el paso anterior al modelo regresor mediante el método `.get_feature_names_out()`

2. Luego, vuelva a reportar el `MAE` sobre el conjunto de validación. [1 puntos]

3. ¿Cómo cambia el error al incluir esta relación? ¿Tenía razón su amigo? [2 puntos]

4. Guarde su modelo en un archivo .pkl [1 punto]

In [56]:
# =============== Pregunta 1 ==================
# Definimos la reelación monótona negativa entre el precio y la cantidad (obtuve el nombre de la columna tras el preprocesamiento con el hint)
monotone_constraints = {"num__price": -1}

# Definimos el pipeline con XGBRegressor y la restricción monótona
pipeline_xgb_mono = Pipeline(steps=[
    ("date_ft", date_ft),          
    ("preprocess", preprocess),      
    ("model", XGBRegressor(random_state=SEED, monotone_constraints=monotone_constraints))
])

# Entrenamos el modelo con la rsetricción monótona
pipeline_xgb_mono.fit(X_train, y_train)

# =============== Pregunta 2 ==================
# Hacemos predicciones en el conjunto de validación
y_val_pred_xgb_mono = pipeline_xgb_mono.predict(X_val)

# Evaluamos el MAE
mae_xgb_mono = mean_absolute_error(y_val, y_val_pred_xgb_mono)

# Mostramos el MAE en pantalla
print(f"MAE validación (XGBRegressor con restricción monótona): {mae_xgb_mono:.3f}")

# =============== Pregunta 4 ==================
# Guardamos el archivo en un .pkl
joblib.dump(pipeline_xgb_mono, 'pipeline_xgb_mono.pkl')

MAE validación (XGBRegressor con restricción monótona): 2520.282


['pipeline_xgb_mono.pkl']

**Respuestas:**

**Pregunta 3:** El error aumentó desde $2405$ (XGBRegressor normal) hasta $2520$ (XGBRegressor con una relación monótona negativa entre el precio y la cantidad). Debido a esto, se puede concluir que el último modelo es peor, y por tanto el amigo no tenía razón, pues si este fuese el caso el modelo debería haber mejorado.

## 1.3 Optimización de Hiperparámetros con Optuna (20 puntos)

<p align="center">
  <img src="https://media.tenor.com/fmNdyGN4z5kAAAAi/hacking-lucy.gif">
</p>

Luego de presentarle sus resultados, Fiu le pregunta si es posible mejorar *aun más* su modelo. En particular, le comenta de la optimización de hiperparámetros con metodologías bayesianas a través del paquete `optuna`. Como usted es un aficionado al entrenamiento de modelos de ML, se propone implementar la descabellada idea de su jefe.

A partir de la mejor configuración obtenida en la sección anterior, utilice `optuna` para optimizar sus hiperparámetros. En particular, se pide que su optimización considere lo siguiente:

- Fijar una semilla en las instancias necesarias para garantizar la reproducibilidad de resultados
- Utilice `TPESampler` como método de muestreo
- De `XGBRegressor`, optimice los siguientes hiperparámetros:
    - `learning_rate` buscando valores flotantes en el rango (0.001, 0.1)
    - `n_estimators` buscando valores enteros en el rango (50, 1000)
    - `max_depth` buscando valores enteros en el rango (3, 10)
    - `max_leaves` buscando valores enteros en el rango (0, 100)
    - `min_child_weight` buscando valores enteros en el rango (1, 5)
    - `reg_alpha` buscando valores flotantes en el rango (0, 1)
    - `reg_lambda` buscando valores flotantes en el rango (0, 1)
- De `OneHotEncoder`, optimice el hiperparámetro `min_frequency` buscando el mejor valor flotante en el rango (0.0, 1.0)

Para ello se pide los siguientes pasos:
1. Implemente una función `objective()` que permita minimizar el `MAE` en el conjunto de validación. Use el método `.set_user_attr()` para almacenar el mejor pipeline entrenado. [10 puntos]
2. Fije el tiempo de entrenamiento a 5 minutos. [1 punto]
3. Optimizar el modelo y reportar el número de *trials*, el `MAE` y los mejores hiperparámetros encontrados. ¿Cómo cambian sus resultados con respecto a la sección anterior? ¿A qué se puede deber esto? [3 puntos]
4. Explique cada hiperparámetro y su rol en el modelo. ¿Hacen sentido los rangos de optimización indicados? [5 puntos]
5. Guardar su modelo en un archivo .pkl [1 punto]

In [57]:
# Código entregado
import optuna
from optuna.samplers import TPESampler
optuna.logging.set_verbosity(optuna.logging.WARNING)

# Importamos librerías necesarias
import time

# =============== Pregunta 1 ==================
def objective(trial):
    
    # Definimos los hiperparámetros a optimizar para XGBRegressor
    learning_rate = trial.suggest_float('learning_rate', 0.001, 0.1)
    n_estimators = trial.suggest_int('n_estimators', 50, 1000)
    max_depth = trial.suggest_int('max_depth', 3, 10)
    max_leaves = trial.suggest_int('max_leaves', 0, 100)
    min_child_weight = trial.suggest_int('min_child_weight', 1, 5)
    reg_alpha = trial.suggest_float('reg_alpha', 0, 1)
    reg_lambda = trial.suggest_float('reg_lambda', 0, 1)
    
    # Definimos los hiperparámetros a optimizar para OneHotEncoder
    min_frequency = trial.suggest_float('min_frequency', 0.0, 1.0)
    
    # Definimos de nuevo el preprocess para agregar min_frequency
    preprocess = ColumnTransformer(
        transformers=[
            ("num", StandardScaler(), numeric_cols),  # Aplicamos StandardScaler a las columnas numéricas
            ("cat", OneHotEncoder(handle_unknown="ignore", sparse_output=False, min_frequency=min_frequency), categorical_cols)  # Aplicamos OneHotEncoder a las categóricas    
        ],
        remainder="drop"
    )
    
    # Creamos el pipeline

    model = Pipeline(steps=[
        ('date_ft', date_ft),
        ('preprocess', preprocess),
        ('regressor', XGBRegressor(
            learning_rate=learning_rate,
            n_estimators=n_estimators,
            max_depth=max_depth,
            max_leaves=max_leaves,
            min_child_weight=min_child_weight,
            reg_alpha=reg_alpha,
            reg_lambda=reg_lambda,
            random_state=SEED
        ))
    ])

    # Entrenamos el modelo
    model.fit(X_train, y_train)

    # Hacemos predicciones en el conjunto de validación
    y_pred = model.predict(X_val)

    # Calculamos el MAE
    mae = mean_absolute_error(y_val, y_pred)

    # Almacenamos el mejor modelo entrenado en el objeto 'trial'
    trial.set_user_attr("best_model", model)

    return mae  # Devolvemos el MAE para minimizarlo

# ================ Preguntas 2 y 3 ==================

# Definimos el sampler para la optimización
sampler = TPESampler(seed=SEED)

# Creamos el estudio de Optuna
study = optuna.create_study(direction='minimize', sampler=sampler)

# Realizamos la optimización con 300 trials
study.optimize(objective, n_trials=300, timeout=300, show_progress_bar=True)  # Acá está la pregunta 2 (timeout=300)

# Obtenemos el número de trials realizados y los mostramos en pantalla
num_trials = len(study.trials)
print("Número de trials realizados:", num_trials)

# Obtenemos el MAE dl mejor modelo y lo mostramos en pantalla
best_mae = study.best_value
print(f"Mejor MAE en validación: {best_mae:.3f}")

# Obtenemos los mejores parámetros encontrados por Optuna y los mostramos en pantalla
best_params = study.best_params
print("Mejores parámetros:", best_params)

# ================ Pregunta 5 ==================
# Recuperamos el mejor modelo entrenado con el método dado en el enunciado
best_model = study.best_trial.user_attrs['best_model']

# Guardamos el mejor modelo en un archivo .pkl
joblib.dump(best_model, 'best_model_optuna.pkl')

  0%|          | 0/300 [00:00<?, ?it/s]

Número de trials realizados: 221
Mejor MAE en validación: 1962.432
Mejores parámetros: {'learning_rate': 0.0938116000800351, 'n_estimators': 836, 'max_depth': 10, 'max_leaves': 82, 'min_child_weight': 5, 'reg_alpha': 0.1690492685905627, 'reg_lambda': 0.6552646336435201, 'min_frequency': 0.02025791454140752}


['best_model_optuna.pkl']

**Respuestas:**

**Pregunta 3:** El MAE mejoró considerablemnte con respecto a la parte anterior, pues pasó desde 2405 (XGB por defecto) hasta 1967 (Optuna). La razón de esta mejora es porque al optimizar hiperparámetros se ajustan en simultáneo el ritmo del aprendizaje (`leearning_rate`), la capacidad del modelo (`n_estimators` y `max_depth`) y la regularización (`reg_alpha` y `reg_lambda`), mientras controla el ruido de categorías raras con `min_frequency` en el OneHotEncoder. Este equilibrio que obtine optuna baja el sesgo sin disparar la varianza, lo que hace que el modelo mejore considerablemeent.

**Pregunta 4:** 

- `learning_rate`: Es el tamaño de paso por iteración. Si este número ese bajo, el modelo aprende más lento, pero suele generalizar mejor, mientras que si este número es alto, el modelo converge rápido, pero puede sobrajustar. El rango $(0.001-0.1)$ es estándar para regresión.
- `n_estimators`: Es el número de árboles a utilizar por XGBoost. Más árboles compensan *learning_rates* más bajos. El rango de $(50,1000)$ es suficiente para cubrir modelos livianos y complejos
- `max_depth`: Es la profundidad máxima de cada uno de los árboles. Controlan la complejidad. El rango $(3-10)$ funciona bien.
- `max_leaves`: Es el límite de hojas por cada árbol. Controla el tamaño efectivo del árbol, donde $0$ equivale a un árbol sin límit de hojas. El rango $(0-100)$ es razonable
- `min_child_weight`: Es el mínimo de peso de un nodo hijo. Mientras más alto sa más splits hay y por tanto menos sobreajuste. El rango $(1-5)$ es bastante conservador.
- `reg_alpha`: Es la regularización $L1$. Ayuda a podar pesos. El rango $(0,1)$ es un rango prudente, pero a veces se puede explorar hasta $10$ o más.
- `reg_lambda`: Es la regularización $L2$. Ayuda a suavizar los pesos. El rango $(0,1)$ es un rango prudente, pero a veces se puede explorar hasta $10$ o más.
- `min_frequency`: Es el umbral para agrupar categorías raras en una columna llamada "infrequent". Reduce dimensionalidad y varianza y ayuda con a mejorar la estabilidad con colas largas de categorías. El rango dw $(0,1)$ es el típico que se utiliza, donde $0$ no agrupa nada, entre $0.05 y 0.1$ hay pocas agrupaciones, y valores cercanos a $1$ significan que se agrupa todo. El rango es amplio para poder decidir de buena manera.

En síntesis, todos los rangos son coherentes para el modelo estudiado. Lo único que podría aumentarse más serían los valores de `reg_alpha` y `reg_lambda`, pero de todas maneras están en un buen rango.

## 4. Optimización de Hiperparámetros con Optuna y Prunners (17 puntos)

<p align="center">
  <img src="https://i.pinimg.com/originals/90/16/f9/9016f919c2259f3d0e8fe465049638a7.gif">
</p>

Después de optimizar el rendimiento de su modelo varias veces, Fiu le pregunta si no es posible optimizar el entrenamiento del modelo en sí mismo. Después de leer un par de post de personas de dudosa reputación en la *deepweb*, usted llega a la conclusión que puede cumplir este objetivo mediante la implementación de **Prunning**.

Vuelva a optimizar los mismos hiperparámetros que la sección pasada, pero esta vez utilizando **Prunning** en la optimización. En particular, usted debe:

1. Responder: ¿Qué es prunning? ¿De qué forma debería impactar en el entrenamiento? [2 puntos]
2. Redefinir la función `objective()` utilizando `optuna.integration.XGBoostPruningCallback` como método de **Prunning** [10 puntos]
3. Fijar nuevamente el tiempo de entrenamiento a 5 minutos [1 punto]
4. Reportar el número de *trials*, el `MAE` y los mejores hiperparámetros encontrados. ¿Cómo cambian sus resultados con respecto a la sección anterior? ¿A qué se puede deber esto? [3 puntos]
5. Guardar su modelo en un archivo .pkl [1 punto]

Nota: Si quieren silenciar los prints obtenidos en el prunning, pueden hacerlo mediante el siguiente comando:

```
optuna.logging.set_verbosity(optuna.logging.WARNING)
```

De implementar la opción anterior, pueden especificar `show_progress_bar = True` en el método `optimize` para *más sabor*.

Hint: Si quieren especificar parámetros del método .fit() del modelo a través del pipeline, pueden hacerlo por medio de la siguiente sintaxis: `pipeline.fit(stepmodelo__parametro = valor)`

Hint2: Este <a href = https://stackoverflow.com/questions/40329576/sklearn-pass-fit-parameters-to-xgboost-in-pipeline>enlace</a> les puede ser de ayuda en su implementación

In [58]:
!pip install optuna-integration[xgboost]

In [59]:
# Importamos la librería necesaria para el pruning
from optuna.integration import XGBoostPruningCallback

# Silenciamos los prints obtenidos en l pruning
optuna.logging.set_verbosity(optuna.logging.WARNING)

# Redefinimos la función objective utilizando Pruning
def objective(trial):
    
    # Definimos los hiperparámetros a optimizar para XGBRegressor
    learning_rate = trial.suggest_float('learning_rate', 0.001, 0.1)
    n_estimators = trial.suggest_int('n_estimators', 50, 1000)
    max_depth = trial.suggest_int('max_depth', 3, 10)
    max_leaves = trial.suggest_int('max_leaves', 0, 100)
    min_child_weight = trial.suggest_int('min_child_weight', 1, 5)
    reg_alpha = trial.suggest_float('reg_alpha', 0, 1)
    reg_lambda = trial.suggest_float('reg_lambda', 0, 1)
    
    # Definimos los hiperparámetros a optimizar para OneHotEncoder
    min_frequency = trial.suggest_float('min_frequency', 0.0, 1.0)
    
    # Definimos de nuevo el preprocess para agregar min_frequency
    preprocess = ColumnTransformer(
        transformers=[
            ("num", StandardScaler(), numeric_cols),  # Aplicamos StandardScaler a las columnas numéricas
            ("cat", OneHotEncoder(handle_unknown="ignore", sparse_output=False, min_frequency=min_frequency), categorical_cols)  # Aplicamos OneHotEncoder a las categóricas    
        ],
        remainder="drop"
    )
    
    # Creamos un pipeline con los primeros dos pasos
    prep = Pipeline(steps=[
        ('date_ft', date_ft),
        ('preprocess', preprocess)
    ])
    
    # Fit-transform de train y transform de val
    X_train_transformed = prep.fit_transform(X_train, y_train)
    X_val_transformed = prep.transform(X_val)
    
    # Usamos XGBoostPruningCallback para el prunning (usamos MAE pues es la métrica de interés)
    pruning_callback = XGBoostPruningCallback(trial, "validation_0-mae")
    
    # Definimos el regressor
    regressor = XGBRegressor(
        learning_rate=learning_rate,
        n_estimators=n_estimators,
        max_depth=max_depth,
        max_leaves=max_leaves,
        min_child_weight=min_child_weight,
        reg_alpha=reg_alpha,
        reg_lambda=reg_lambda,
        random_state=SEED
    )
    
    # Fiteamos el regressor con los datos transformados
    regressor.fit(X_train_transformed, y_train, eval_set=[(X_val_transformed, y_val)], eval_metric='mae', verbose=False, callbacks=[pruning_callback], early_stopping_rounds=50)

    # Hacemos predicciones en el conjunto de validación
    y_pred = regressor.predict(X_val_transformed)

    # Calculamos el MAE
    mae = mean_absolute_error(y_val, y_pred)
    
    # Definimos el modelo entero
    full_model = Pipeline(steps=[("prep", prep), ("regressor", regressor)])

    # Almacenamos el mejor modelo entrenado en el objeto 'trial'
    trial.set_user_attr("best_model", full_model)

    return mae  # Devolvemos el MAE para minimizarlo

# Definimos el sampler para la optimización
sampler = TPESampler(seed=SEED)

# Creamos el estudio de Optuna
study = optuna.create_study(direction='minimize', sampler=sampler)

# Realizamos la optimización con 300 trials
study.optimize(objective, n_trials=300, timeout=300, show_progress_bar=True)  # Acá fijamos el timeout de 5 minutos

# Obtenemos el número de trials realizados y los mostramos en pantalla
num_trials = len(study.trials)
print("Número de trials realizados:", num_trials)

# Obtenemos el MAE dl mejor modelo y lo mostramos en pantalla
best_mae = study.best_value
print(f"Mejor MAE en validación: {best_mae:.3f}")

# Obtenemos los mejores parámetros encontrados por Optuna y los mostramos en pantalla
best_params = study.best_params
print("Mejores parámetros:", best_params)

# No lo pedían, pero imprimí estadísticas de prunning para ver si estaba funcionando
n_pruned   = sum(t.state == optuna.trial.TrialState.PRUNED for t in study.trials)
n_complete = sum(t.state == optuna.trial.TrialState.COMPLETE for t in study.trials)
print(f"Trials podados: {n_pruned} | Completos: {n_complete}")

# Recuperamos el mejor modelo entrenado con el método dado en el enunciado
best_model = study.best_trial.user_attrs['best_model']

# Guardamos el mejor modelo en un archivo .pkl
joblib.dump(best_model, 'best_model_optuna_pruning.pkl')

  0%|          | 0/300 [00:00<?, ?it/s]

c:\Users\samot\miniforge3\Lib\site-packages\xgboost\sklearn.py:889: UserWarning:

`eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.

c:\Users\samot\miniforge3\Lib\site-packages\xgboost\sklearn.py:889: UserWarning:

`early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.

c:\Users\samot\miniforge3\Lib\site-packages\xgboost\sklearn.py:889: UserWarning:

`callbacks` in `fit` method is deprecated for better compatibility with scikit-learn, use `callbacks` in constructor or`set_params` instead.

c:\Users\samot\miniforge3\Lib\site-packages\xgboost\sklearn.py:889: UserWarning:

`eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.

c:\Users\samot\miniforge3\Lib\site-packages\xgboost\sklearn.py:889: User

Número de trials realizados: 240
Mejor MAE en validación: 1940.668
Mejores parámetros: {'learning_rate': 0.0852489073189092, 'n_estimators': 746, 'max_depth': 10, 'max_leaves': 97, 'min_child_weight': 4, 'reg_alpha': 0.44120515393754706, 'reg_lambda': 0.676027791141889, 'min_frequency': 0.0681088695754471}
Trials podados: 185 | Completos: 55


['best_model_optuna_pruning.pkl']

**Respuestas:**

**Pregunta 1:** Pruning consiste en el corte anticipado de trials durante la optimización de hiperparámetros. Optuna observa la métrica intermedia del trial (MAE en este caso por árbol en eval_set) y, si va peor que un umbral se interrumpe ese trial antes de terminar. 

El impacto esperado es un menor tiempo computacional efectivo, pues no se procesan del todo configuraciones malas. Es decir, se podan las malas configuraciones para pasar a las siguientes. Esto trae consigo una mayor exploración útil bajo un mismo presupuesto de tiempo. Es decir, se pueden hacer más trials, obteniendo un mejor MAE en el mismo tiempo de entrenamiento.

**Pregunta 4:** Con respecto a la parte anterior vemos dos cosas relevantes: En primer lugar, el número de Trials aumentó desde $221$ hasta $240$, y en segundo lugar el MAE disminuyó desde $1962$ hasta $1940$. Además, de los árboles vistos, $185$ fueron podados y $55$ fueron completados.

La razón de esto es que con pruning se pudieron explorar más configuraciones en el mismo tiempo, ya que se cortaron tempranamente los trials que iban mal. Además, el MAE mejoró un poco debido a que se tuvo más tiempo para explorar debido al pruning. 

Los hiperparámetros obtenidos como tal también cambiaron un poco. En particular, `min_frequency` pasó desde $0.020$ hasta $0.068$, lo cual implica que hay menos categorías raras y menor varianza. ``reg_alpha`` pasó desde $0.17$ hasta $0.44$, por lo que hay menos sobreajuste. ``learning_rate`` bajó desde $0.094$ hasta $0.085$ y `n_estimators` pasó dsede $836$ hasta $746$. Esto resulta en un entranemiento más contenido y con regularización efectiva. Finalmente, `max_leaves` sube desde $82$ a $97$ y `min_child_weight` baja desde $5$ hasta $4$, lo cual significa que el modelo retiene algo más de flexibilidad, pero compensada por la regularización y el filtrado de categorías.

En conclusión, el pruning ayudó bastante pues se aumentó el número de trials realizados y se disminuyó el MAE.

## 5. Visualizaciones (5 puntos)

<p align="center">
  <img src="https://media.tenor.com/F-LgB1xTebEAAAAd/look-at-this-graph-nickelback.gif">
</p>


Satisfecho con su trabajo, Fiu le pregunta si es posible generar visualizaciones que permitan entender el entrenamiento de su modelo.

A partir del siguiente <a href = https://optuna.readthedocs.io/en/stable/tutorial/10_key_features/005_visualization.html#visualization>enlace</a>, genere las siguientes visualizaciones:

1. Gráfico de historial de optimización [1 punto]
2. Gráfico de coordenadas paralelas [1 punto]
3. Gráfico de importancia de hiperparámetros [1 punto]

Comente sus resultados:

4. ¿Desde qué *trial* se empiezan a observar mejoras notables en sus resultados? [0.5 puntos]
5. ¿Qué tendencias puede observar a partir del gráfico de coordenadas paralelas? [1 punto]
6. ¿Cuáles son los hiperparámetros con mayor importancia para la optimización de su modelo? [0.5 puntos]

In [60]:
# Importamos las librerías necesarias
from optuna.visualization import plot_optimization_history, plot_intermediate_values, plot_param_importances
# =============== Pregunta 1 ==================
plot_optimization_history(study)

In [61]:
# =============== Pregunta 2 ==================
plot_intermediate_values(study)

In [62]:
# =============== Pregunta 3 ==================
plot_param_importances(study)

**Respuestas:**

**Pregunta 4:** Alrededor del trial $10$ se ve una caída fuerte del MAE (pasa desde $5000-6000$ hasta $2200$). Luego hay otra mejora relevante alrededor del trial $20-25$, en donde el MAE baja y se estabiliza alrededor de $2000$.

**Pregunta 5:** En primer lugar se puede apreciar como casi todos los trials bajan su MAE de manera muy rápida al inicio (primeras $0-50$ rondas). Por otro lado, también se puede ver una convergencia temprana de los trials, pues todos se estabilizan cerca de $2000$ antes de las $200-250$ rondas, mientras que después de esto hay decrecimientos no tan sustanciales. Otra cosa que se puede observar es que los trials malos que se quedan pegados con valores de MAE entre $5000$ y $9000$ son podados de forma temprana. Finalmente, se puede observar una dispersión que se estrecha, pues al principio hay gran variabilidad entre curvas, pero hacia las $200$ rondas casi todas las trayectorias convergen a valores similares.

**Pregunta 6:** Se puede observar que `min_frequency` y `learning_rate` son los hiperparámetros más importantes, con importancias relativas de $0.77$ y $0.13$ respectivamente. Aún así, claramente `min_frequency` es el hiperparámetro más relevante por lejos. Seguido a estos dos, le siguen `reg_lambda`, `reg_alpha` y `n_estimators`, con valores de relevancai de $0.04$, $0.03$ y $0.02$ respectivamente, y luego `max_leaves`, `max_depth` y `min_child_weight`, todos con relevancias menores a $0.01$.

## 6. Síntesis de resultados (3 puntos)

Finalmente:

1. Genere una tabla resumen del MAE en el conjunto de validación obtenido en los 5 modelos entrenados desde Baseline hasta XGBoost con Constraints, Optuna y Prunning. [1 punto]
2. Compare los resultados de la tabla y responda, ¿qué modelo obtiene el mejor rendimiento? [0.5 puntos]
3. Cargue el mejor modelo, prediga sobre el conjunto de **test** y reporte su MAE. [0.5 puntos]
4. ¿Existen diferencias con respecto a las métricas obtenidas en el conjunto de validación? ¿Porqué puede ocurrir esto? [1 punto]

In [72]:
# Importamos las librerías necesarias
from pathlib import Path

# ================ Pregunta 1 ==================
# Rutas de los modelos
model_paths = {
    "Baseline – DummyRegressor (mean)": "pipeline_dummy.pkl",
    "XGBRegressor (default)": "pipeline_xgb.pkl",
    "XGBRegressor + Monotonicidad": "pipeline_xgb_mono.pkl",
    "XGBRegressor + Optuna (mejor config)": "best_model_optuna.pkl",
    "XGBRegressor + Optuna + Pruning": "best_model_optuna_pruning.pkl",
}

# Función para cargar y evaluar modelos
def score_model(model_name, path_str):
    p = Path(path_str)
    if not p.exists():
        return {
            "Modelo": model_name,
            "MAE_validación": None,
        }
    model = joblib.load(path_str)
    y_pred = model.predict(X_val)
    mae = mean_absolute_error(y_val, y_pred)
    return {
        "Modelo": model_name,
        "MAE_validación": mae,
    }

# Mostramos el MAE en el conjunto de validación para cada modelo
rows = [score_model(name, path) for name, path in model_paths.items()]
df = pd.DataFrame(rows)
print("Resumen MAE en validación (modelos guardados):")
display(df)

# ================ Pregunta 3 ==================
# Recuperamos el mejor modelo entrenado
best_model = joblib.load('best_model_optuna_pruning.pkl')

# Hacemos predicciones en el conjunto de test
y_test_pred = best_model.predict(X_test)

# Evaluamos el MAE
mae_test = mean_absolute_error(y_test, y_test_pred)

# Mostramos el MAE en pantalla
print(f"MAE test (mejor modelo con pruning): {mae_test:.3f}")

Resumen MAE en validación (modelos guardados):


Modelo  MAE_validación
0      Baseline – DummyRegressor (mean)    13543.961388
1                XGBRegressor (default)     2402.355308
2          XGBRegressor + Monotonicidad     2520.281914
3  XGBRegressor + Optuna (mejor config)     1962.431980
4       XGBRegressor + Optuna + Pruning     1940.668416

MAE test (mejor modelo con pruning): 1907.861


**Respuestas:**

**Pregunta 2:** El modelo que obtuvo el mejor rendimiento para la métrica analizada (MAE) fue el XGBRegressor con optimización de hiperparámetros con Optuna y con pruning. Esto pues es el modelo que tiene un menor MAE de entre todos los modelos.

**Prgunta 4:** Efectivamente sí hay diferencia con respecto a las métricas obtenidas en el conjunto de validación. El MAE disminuyó desde $1940$ (validación) hasta $1907$ (conjunto de test). Esto ocurre más que nada gracias a una variabilidad muestral. Debido a que el conjunto de test es otro conjunto de datos diferente al de validación, por puro azar puede resultar un poco mejor nuestro modelo en este conjunto de datos (por ejemplo pueden haber menos outliers o menos ruido), lo cual hace que el MAE disminuya.

# Conclusión
Exito!
<p align="center">
  <img src="https://i.pinimg.com/originals/55/3d/42/553d42bea9b10e0662a05aa8726fc7f4.gif">
</p>